In [122]:
import numpy as np
import copy
from sklearn.neural_network import MLPRegressor
from numpy.random import *
from operator import itemgetter

# 1.InputFieldData

In [359]:
def sortAgentsPosInfo(agents_pos_list_with_num):
    np_agents_pos_list_with_num = np.asarray(agents_pos_list_with_num)
    sorted_np_agents_pos_list_with_num = np.array(sorted(np_agents_pos_list_with_num,key=itemgetter(1)))
    agents_pos_list = []
    for pos_info in sorted_np_agents_pos_list_with_num:
        agents_pos_list.append(pos_info[0])
    print("agents_pos_list = {0}".format(agents_pos_list))
    return agents_pos_list

In [360]:
def inputFieldData(text_path):
    f = open(text_path)
    line = f.readline()
    line_count = 1
    field_size = int(len(line) / 2)
    field = np.empty((0,field_size),int)
    agents_pos_list = []
    while line:
        last_idx = line.find("\n")
        field_row = np.array([])
        for i in range(0,last_idx,2):
            field_row = np.append(field_row,int(line[i]))
            if int(line[i]) % 2 == 0 and int(line[i]) != 0:
                agent_data = np.array([np.array([line_count-1,int(i/2)]),int(line[i])])
                agents_pos_list.append(agent_data)
        field = np.append(field,np.array([field_row]),axis=0)
        line = f.readline()
        line_count += 1
    f.close()
    print("init field = \n {0}".format(field))
    agents_pos_list = sortAgentsPosInfo(agents_pos_list)
    return field,agents_pos_list

In [361]:
init_field,agents_pos_list = inputFieldData("test.txt")
field_row = len(init_field[0])
field_col = len(init_field)

init field = 
 [[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  2.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]
agents_pos_list = [array([1, 5]), array([1, 3]), array([4, 3])]


# 2.DecideActions

In [362]:
def moveToNextPos(pos,action):
    if action == 0:
        next_pos = [pos[0]-1,pos[1]]
    elif action == 1:
        next_pos = [pos[0],pos[1]+1]
    elif action == 2:
        next_pos = [pos[0]+1,pos[1]]
    elif action== 3:
        next_pos = [pos[0],pos[1]-1]
    else:
        next_pos = [pos[0],pos[1]]
    return next_pos

In [363]:
def buildNetwork(X_train,y_train):
    clf = MLPRegressor(solver="adam",random_state=1,max_iter=1000,hidden_layer_sizes=(20,50,10))
    print("X_train.shape = {0} , y_train.shape = {1}".format(X_train.shape,y_train.shape))
    clf.fit(X_train,y_train)
    return clf

In [364]:
def checkActions(pred_actions,field,poses):
    for i in range(len(pred_actions)):
        pos = poses[i]
        pred_action = pred_actions[i]
        next_pos = moveToNextPos(pos,pred_action)
        #行動先が壁の場合
        while field[next_pos[0],next_pos[1]] == 1:
            pred_action = int(pred_action + rand() * 3 + 1) % 4
            next_pos = moveToNextPos(pos,pred_action)
        pred_actions[i] = pred_action
    return pred_actions

In [365]:
def predictActions(clf,field):
    X_test = np.asarray(field).reshape(1,field_row*field_col)
    actions = clf.predict(X_test)[0]
    for i in range(len(actions)):
        actions[i] = int(actions[i])
        
    if rand() < 0.3:
        for i in range(len(actions)):
            actions[i] = int(actions[i] + rand() * 3 + 1) % 4
    return actions

In [366]:
def updateField(poses,next_poses,field):
    for i in range(len(agents_pos_list)):
        pos = poses[i]
        next_pos = next_poses[i]
#         print(pos,next_pos)
        #エージェントがいずれかの方向に進行する場合
        if pos != next_pos:
            if field[pos[0],pos[1]] % 2 == 0:
                field[pos[0],pos[1]] = 0
                field[next_pos[0],next_pos[1]] = i*2 + 2

In [367]:
def createTrainData(init_field,init_poses):
    field_data = [copy.deepcopy(init_field)]
    field = copy.deepcopy(init_field)
    poses = init_poses
    action_data = []
    for i in range(FIND_ROOT_MAX_LOOP):
        if clf != None:
            pred_actions = predictActions(clf,field)
        else:
            pred_actions = [int(rand()*4) for i in range(len(agents_pos_list))]
        #予測したアクションに対してチェックを行い，壁や他エージェントにぶつかる挙動を変更する
        actions = checkActions(pred_actions,field,poses)
        #タイムステップ毎のアクションを保持するaction_dataの末尾に次の行動を追加
        action_data.append(actions)
        #actionsを元に次のfieldへと遷移させる
        next_poses = []
        for j in range(len(agents_pos_list)):
            next_poses.append(moveToNextPos(poses[j],actions[j]))
        updateField(poses,next_poses,field)
        field_data.append(copy.deepcopy(field))
        poses = next_poses
    for i in range(30):
        print(field_data[i])
        print("\n")

In [368]:
FIND_ROOT_MAX_LOOP = 100
clf = None
path_count = 1e+7
agents_poses = []
for agents_pos in agents_pos_list:
    agents_poses.append(agents_pos.tolist())
for i in range(2000):
    init_poses = agents_poses
    create_flag = False
    if (i+1) % 100 == 0:
        print("epoch = {0}".format(i+1))
    createTrainData(init_field,init_poses)

[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  2.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  4.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  2.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  6.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  4.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  2.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  2.  0.  1.]
 [ 1.  4.  1.  7.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0

 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  2.  0.  0.  0.  0.  0.  4.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  6.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  2.  0.  0.  0.  4.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  6.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  2.  0.  0.  0.  4.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  2.  1.  0.  0.  4.  1.]
 [ 1.  0.  1.



[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  4.  1.  7.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  6.  0.  0.  2.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  0.  0.  1.]
 [ 1.  4.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  6.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  2.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  2.  1.  0.  1.]
 [ 1.  6.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  0.  0.  1.]
 [ 1.  4.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  6.  1. 


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  6.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  2.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  4.  1.  3.  0.  0.  1.]
 [ 1.  6.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  2.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  4.  1.  0.  1.  0.  1.]
 [ 1.  6.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  2.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  

 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  2.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  4.  1.]
 [ 1.  6.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  2.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  4.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  6.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  2.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  4.  1.]
 [ 1.  6.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  2.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  6.  1.

...


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  2.  0.  4.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  6.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  4.  0.  1.]
 [ 1.  0.  1.  0.  1.  2.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  6.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  2.  0.  4.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  6.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  2.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  4.  1.]
 [ 1.  0.  1.  

[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  2.  0.  0.  0.  1.]
 [ 1.  0.  1.  4.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  6.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  2.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  6.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  6.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  4



[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  4.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  2.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  6.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  2.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  4.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  0.  2.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  6.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  0.  2.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1. 

[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  0.  2.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  6.  4.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  0.  4.  0.  2.  0.  0.  1.]
 [ 1.  0.  1.  7.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  6.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  0.  4.  0.  0.  0.  2.  0.  1.]
 [ 1.  0.  1.  7.  1.  3.  0.  0.  1.]
 [ 1.  0.  1.  6.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0.  0.  0.  1.  0.  1.]
 [ 1.  0.  0.  0.  0.  0.  5.  0.  1.]
 [ 1.  1.  1.  1.  1.  1.  1.  1.  1.]]


[[ 1.  1.  1.  1.  1.  1.  1.  1.  1.]
 [ 1.  4.  0.  0.  0.  0.  0.  0.  1.]
 [ 1.  0.  1.  6.  1.  3.  2.  0.  1.]
 [ 1.  0.  1.  0.  1.  0.  1.  0.  1.]
 [ 1.  0.  1.  0

KeyboardInterrupt: 